# Unit 6: Advantage Actor Critic (A2C) using Robotics Simulations with PyBullet and Panda-Gym 🤖

[Panda-Gym](https://github.com/qgallouedec/panda-gym), you're going **to train a robotic arm** (Franka Emika Panda robot) to perform a task:
- `Reach`: the robot must place its end-effector at a target position.

After that, you'll be able **to train in other robotics environments**.


In [14]:
%%capture
!apt install python-opengl
!apt install ffmpeg
!apt install xvfb
!pip3 install pyvirtualdisplay

In [15]:
# Virtual display
from pyvirtualdisplay.display import Display

virtual_display = Display(visible=False, size=(1400, 900))
virtual_display.start()

In [16]:
!pip install -r https://raw.githubusercontent.com/huggingface/deep-rl-class/main/notebooks/unit6/requirements-unit6.txt

## Import the packages 📦

In [17]:
import pybullet_envs
import panda_gym
import gym

import os

from huggingface_sb3 import load_from_hub, package_to_hub

from stable_baselines3 import A2C
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize
from stable_baselines3.common.env_util import make_vec_env

from huggingface_hub._login import notebook_login

To be able to share your model with the community there are three more steps to follow:

1️⃣ (If it's not already done) create an account to HF ➡ https://huggingface.co/join

2️⃣ Sign in and then, you need to store your authentication token from the Hugging Face website.
- Create a new token (https://huggingface.co/settings/tokens) **with write role**


- Copy the token 
- Run the cell below and paste the token

In [18]:
notebook_login()
!git config --global credential.helper store

## Take a coffee break ☕
- You already trained your first robot that learned to move congratutlations 🥳!
- It's **time to take a break**. Don't hesitate to **save this notebook** `File > Save a copy to Drive` to work on this second part later.


## Environment 2: PandaReachDense-v2 🦾



In `PandaReachDense-v2` the robotic arm must place its end-effector at a target position (green ball).



In [19]:
import gym

env_id = "PandaReachDense-v2"

# Create the env
env = gym.make(env_id)

# Get the state space and action space
s_size = env.observation_space.shape
a_size = env.action_space

In [20]:
print("_____OBSERVATION SPACE_____ \n")
print("The State Space is: ", s_size)
print("Sample observation", env.observation_space.sample()) # Get a random observation

_____OBSERVATION SPACE_____ 

The State Space is:  None
Sample observation OrderedDict([('achieved_goal', array([-2.755843 , -0.7127161,  8.234856 ], dtype=float32)), ('desired_goal', array([-5.952609, -9.438881,  9.54923 ], dtype=float32)), ('observation', array([ 7.563415  ,  7.94455   , -3.7694964 , -9.534212  , -8.491451  ,
        0.01499274], dtype=float32))])


The observation space **is a dictionary with 3 different elements**:
- `achieved_goal`: (x,y,z) position of the goal.
- `desired_goal`: (x,y,z) distance between the goal position and the current object position.
- `observation`: position (x,y,z) and velocity of the end-effector (vx, vy, vz).

Given it's a dictionary as observation, **we will need to use a MultiInputPolicy policy instead of MlpPolicy**.

In [21]:
print("\n _____ACTION SPACE_____ \n")
print("The Action Space is: ", a_size)
print("Action Space Sample", env.action_space.sample()) # Take a random action


 _____ACTION SPACE_____ 

The Action Space is:  Box([-1. -1. -1.], [1. 1. 1.], (3,), float32)
Action Space Sample [ 0.5000411  -0.62558055  0.68555754]


The action space is a vector with 3 values:
- Control x, y, z movement

Now it's your turn:

1. Define the environment called "PandaReachDense-v2"
2. Make a vectorized environment
3. Add a wrapper to normalize the observations and rewards. [Check the documentation](https://stable-baselines3.readthedocs.io/en/master/guide/vec_envs.html#vecnormalize)
4. Create the A2C Model (don't forget verbose=1 to print the training logs).
5. Train it for 1M Timesteps
6. Save the model and  VecNormalize statistics when saving the agent
7. Evaluate your agent
8. Publish your trained model on the Hub 🔥 with `package_to_hub`

In [22]:
# 1 - 2
env_id = "PandaReachDense-v2"
env = make_vec_env(env_id, n_envs=4)

# 3
env = VecNormalize(env, norm_obs=True, norm_reward=False, 
clip_obs=10.)

# 4
model = A2C(
    learning_rate=1e-4,
    policy = "MultiInputPolicy",
    env = env,
    verbose=1
    )
# 5
model.learn(2_000_000)

Using cuda device
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 50       |
|    ep_rew_mean        | -11.5    |
| time/                 |          |
|    fps                | 600      |
|    iterations         | 100      |
|    time_elapsed       | 3        |
|    total_timesteps    | 2000     |
| train/                |          |
|    entropy_loss       | -4.24    |
|    explained_variance | 0.977    |
|    learning_rate      | 0.0007   |
|    n_updates          | 99       |
|    policy_loss        | -3.39    |
|    std                | 0.992    |
|    value_loss         | 0.686    |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 50       |
|    ep_rew_mean        | -11.3    |
| time/                 |          |
|    fps                | 590      |
|    iterations         | 200      |
|    time_elapsed       | 6        |
|    total_timesteps

In [24]:
# 6
model_name = "a2c-PandaReachDense-v2"; 
model.save(model_name)
env.save("vec_normalize.pkl") # type: ignore
# 7
from stable_baselines3.common.vec_env import DummyVecEnv, VecNormalize

# Load the saved statistics
eval_env = DummyVecEnv([lambda: gym.make("PandaReachDense-v2")])
eval_env = VecNormalize.load("vec_normalize.pkl", eval_env)

#  do not update them at test time
eval_env.training = False
# reward normalization is not needed at test time
eval_env.norm_reward = False

# Load the agent
model = A2C.load(model_name)

mean_reward, std_reward = evaluate_policy(model, eval_env)

print(f"Mean reward = {mean_reward:.2f} +/- {std_reward:.2f}")

# 8
package_to_hub(
    model=model,
    model_name=f"a2c-{env_id}",
    model_architecture="A2C",
    env_id=env_id,
    eval_env=eval_env,
    repo_id=f"aj555/a2c-{env_id}",
    commit_message="Initial commit",
)

/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Mean reward = -8.16 +/- 2.40
ℹ This function will save, evaluate, generate a video of your agent,
create a model card and push everything to the hub. It might take up to 1min.
This is a work in progress: if you encounter a bug, please open an issue.


/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/panda_gym/pybullet.py:97: UserWarning: The use of the render method is not recommended when the environment has not been created with render=True. The rendering will probably be weird. Prefer making the environment with option `render=True`. For example: `env = gym.make('PandaReach-v2', render=True)`.
  warnings.warn(


Saving video to /tmp/tmpb3fouqqm/-step-0-to-step-1000.mp4


Exception ignored in: <function VecVideoRecorder.__del__ at 0x7ff6e5637550>
Traceback (most recent call last):
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/vec_env/vec_video_recorder.py", line 113, in __del__
    self.close()
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/vec_env/vec_video_recorder.py", line 109, in close
    VecEnvWrapper.close(self)
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/vec_env/base_vec_env.py", line 279, in close
    return self.venv.close()
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/vec_env/base_vec_env.py", line 279, in close
    return self.venv.close()
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/stable_baselines3/common/vec_env/dummy_vec_env.py", line 80, in close
    env.close()
  File "/home/aj/anaconda3/envs/HF_DRL/lib/python3.8/site-packages/gy

...

vec_normalize.pkl:   0%|          | 0.00/3.06k [00:00<?, ?B/s]

Upload 2 LFS files:   0%|          | 0/2 [00:00<?, ?it/s]

a2c-PandaReachDense-v2.zip:   0%|          | 0.00/108k [00:00<?, ?B/s]

ℹ Your model is pushed to the Hub. You can view your model here:
https://huggingface.co/aj555/a2c-PandaReachDense-v2/tree/main/


'https://huggingface.co/aj555/a2c-PandaReachDense-v2/tree/main/'

## Some additional challenges 🏆
The best way to learn **is to try things by your own**! Why not trying  `HalfCheetahBulletEnv-v0` for PyBullet and `PandaPickAndPlace-v1` for Panda-Gym?

If you want to try more advanced tasks for panda-gym, you need to check what was done using **TQC or SAC** (a more sample-efficient algorithm suited for robotics tasks). In real robotics, you'll use a more sample-efficient algorithm for a simple reason: contrary to a simulation **if you move your robotic arm too much, you have a risk of breaking it**.

PandaPickAndPlace-v1: https://huggingface.co/sb3/tqc-PandaPickAndPlace-v1

And don't hesitate to check panda-gym documentation here: https://panda-gym.readthedocs.io/en/latest/usage/train_with_sb3.html

Here are some ideas to achieve so:
* Train more steps
* Try different hyperparameters by looking at what your classmates have done 👉 https://huggingface.co/models?other=https://huggingface.co/models?other=AntBulletEnv-v0
* **Push your new trained model** on the Hub 🔥
